# MONITOREO DE PRECIOS DE CRIPTOMONEDAS A TRAVÉS DE APIs CON ANÁLISIS DE TENDENCIAS

## 1. Acceso a APIS

### 1.1 API: Coingeko

Para el acceso a la [API de Coingecko](https://www.coingecko.com/es), se requería una suscripción de pago para obtener la API key. Debido a esta restricción, la extracción de datos se limitó a la cantidad de información accesible de forma gratuita a través de la página web.

### 1.2 API: CoinMarketCap

Entrando a la página de la [API de CoinMarketCap](https://coinmarketcap.com/api/) nos creamos una cuenta gratuita y hacemos la verificación mediante un enlace al correo electrónico. Una vez verificada la cuenta, accedemos con nuestro usuario y contraseña para que nos diriga a una nueva pestaña llamada "Developers". 
Aqui podemos generar nuestra API Key para poder tener acceso. Nos dirigimos a la [documentación de la API](https://coinmarketcap.com/api/documentation/v1/#section/Endpoint-Overview) en donde poderemos ver la información de las divisas en cryptocurrency, el cual cuenta con 17 endpoints. Trabajaremos con el endpoint "Listings Latest" ya que devuelve una lista paginada de todas las criptomonedas activas con los últimos datos del mercado.


### 1.3 API: CryptoCompare

Cuando ingresamos al link de la [API de CryptoCompare](https://min-api.cryptocompare.com/) creamos un usario para luego hacer la verificación mediante correo electrónico. Una vez loggeados hacemos clic en la opción "API Keys" para poder identificar nuestra Key. Luego nos dirigimos al link de la [documentación] (https://min-api.cryptocompare.com/documentation) para ir a la opción de "News" y luego a "Latest News Articles" con el fin de tener acceso a todos los artículos sobre las criptomonedas en todo el mundo. Muy aparte de esta información, CryptoCompare tambien permite acceder a información histórica de precios, de blockchain, futuros, etc.

## 2. EXTRACCION DE DATOS

### Primera API: coingecko

In [1]:
import requests
import pandas as pd

# URL de la API para obtener monedas con sus datos relevantes
url = "https://api.coingecko.com/api/v3/coins/markets"

# Parámetros de la solicitud
params = {
    'vs_currency': 'usd',   # Monedas en USD
    'order': 'market_cap_desc',  # Ordenar por capitalización
    'per_page': 100,        # Cantidad de monedas por página
    'sparkline': False      # Información de gráficos no solicitada
}

# Función para obtener todas las monedas con datos completos
def obtener_datos_moneda(total_monedas_requeridas, parametros_requeridos):
    monedas_con_datos = []
    page = 1
    while len(monedas_con_datos) < total_monedas_requeridas:
        params['page'] = page
        response = requests.get(url, params=params)
        if response.status_code == 200:
            data = response.json()
            monedas_filtradas = filtrar_datos_completos(data, parametros_requeridos)
            monedas_con_datos.extend(monedas_filtradas)
            page += 1
        else:
            print("Error en la solicitud:", response.status_code)
            print(response.json())
            break
    return monedas_con_datos

# Función para filtrar monedas con datos completos
def filtrar_datos_completos(monedas, parametros_requeridos):
    monedas_con_datos = []
    for moneda in monedas:
        tiene_datos_completos = all(moneda[param] is not None for param in parametros_requeridos)
        if tiene_datos_completos:
            monedas_con_datos.append(moneda)
    return monedas_con_datos

# Parámetros requeridos
parametros_requeridos = ['current_price', 'total_volume', 'market_cap', 'circulating_supply', 'total_supply', 'max_supply', 'ath_date', 'atl_date']

# Obtener las monedas con datos completos
total_monedas_requeridas = 500
monedas_filtradas = obtener_datos_moneda(total_monedas_requeridas, parametros_requeridos)

# Convertir a DataFrame
df_monedas = pd.DataFrame(monedas_filtradas)

# Imprimir la cantidad de datos extraídos
print(f"Datos extraídos: {len(df_monedas)} monedas con datos completos")

Error en la solicitud: 429
{'status': {'error_code': 429, 'error_message': "You've exceeded the Rate Limit. Please visit https://www.coingecko.com/en/api/pricing to subscribe to our API plans for higher rate limits."}}
Datos extraídos: 314 monedas con datos completos


In [2]:
# Mostrar las columnas para CoinGecko
print(df_monedas.columns)

Index(['id', 'symbol', 'name', 'image', 'current_price', 'market_cap',
       'market_cap_rank', 'fully_diluted_valuation', 'total_volume',
       'high_24h', 'low_24h', 'price_change_24h',
       'price_change_percentage_24h', 'market_cap_change_24h',
       'market_cap_change_percentage_24h', 'circulating_supply',
       'total_supply', 'max_supply', 'ath', 'ath_change_percentage',
       'ath_date', 'atl', 'atl_change_percentage', 'atl_date', 'roi',
       'last_updated'],
      dtype='object')


El DataFrame "df_monedas" contendrá las columnas:
- id (identificador único de la moneda).
- symbol (símbolo de la moneda, por ejemplo, "BTC").
- name (nombre de la moneda, por ejemplo, "Bitcoin").
- image (URL del logo de la moneda).
- current_price (precio actual en USD).
- market_cap (capitalización de mercado en USD).
- market_cap_rank (rango según la capitalización de mercado).
- fully_diluted_valuation (valorización completamente diluida en USD).
- total_volume (volumen total de comercio en las últimas 24 horas).
- high_24h (precio más alto alcanzado en las últimas 24 horas).
- low_24h (precio más bajo alcanzado en las últimas 24 horas).
- price_change_24h (cambio en el precio en las últimas 24 horas).
- price_change_percentage_24h (porcentaje de cambio en el precio en las últimas 24 horas).
- market_cap_change_24h (cambio en la capitalización de mercado en las últimas 24 horas).
- market_cap_change_percentage_24h (porcentaje de cambio en la capitalización de mercado en las últimas 24 horas).
- circulating_supply (suministro circulante actual de la moneda).
- total_supply (suministro total de la moneda).
- max_supply (suministro máximo de la moneda).
- ath (precio más alto alcanzado en toda la historia).
- ath_change_percentage (porcentaje de cambio respecto al precio ATH).
- ath_date (fecha en que se alcanzó el precio ATH).
- atl (precio más bajo alcanzado en toda la historia).
- atl_change_percentage (porcentaje de cambio respecto al precio ATL).
- atl_date (fecha en que se alcanzó el precio ATL).
- roi (retorno de inversión en porcentaje).
- last_updated (última fecha de actualización de los datos).

### Segunda API: Coinmarketcap

In [3]:
from requests import Request, Session
from requests.exceptions import ConnectionError, Timeout, TooManyRedirects
import json

url = 'https://pro-api.coinmarketcap.com/v1/cryptocurrency/listings/latest'
parameters = {
  'start':'1',
  'limit':'5000',
  'convert':'USD'
}
headers = {
  'Accepts': 'application/json', # Informa al servidor que esperamos la respuesta en formato JSON.
  'X-CMC_PRO_API_KEY': '64bb4596-fe19-4b50-8048-ee8892f1f527',
}

session = Session()
session.headers.update(headers)

try:
  response = session.get(url, params=parameters)
  data = json.loads(response.text)
  print(data)
except (ConnectionError, Timeout, TooManyRedirects) as e:
  print(e)
  

{'status': {'timestamp': '2024-12-20T00:00:46.829Z', 'error_code': 0, 'error_message': None, 'elapsed': 102, 'credit_count': 23, 'notice': None, 'total_count': 10414}, 'data': [{'id': 1, 'name': 'Bitcoin', 'symbol': 'BTC', 'slug': 'bitcoin', 'num_market_pairs': 11849, 'date_added': '2010-07-13T00:00:00.000Z', 'tags': ['mineable', 'pow', 'sha-256', 'store-of-value', 'state-channel', 'coinbase-ventures-portfolio', 'three-arrows-capital-portfolio', 'polychain-capital-portfolio', 'binance-labs-portfolio', 'blockchain-capital-portfolio', 'boostvc-portfolio', 'cms-holdings-portfolio', 'dcg-portfolio', 'dragonfly-capital-portfolio', 'electric-capital-portfolio', 'fabric-ventures-portfolio', 'framework-ventures-portfolio', 'galaxy-digital-portfolio', 'huobi-capital-portfolio', 'alameda-research-portfolio', 'a16z-portfolio', '1confirmation-portfolio', 'winklevoss-capital-portfolio', 'usv-portfolio', 'placeholder-ventures-portfolio', 'pantera-capital-portfolio', 'multicoin-capital-portfolio', 'p

In [4]:
# Crear una lista de diccionarios con la información relevante de cada criptomoneda
cryptos_data = []

for crypto in data['data']:
    cryptos_data.append({
        'Name': crypto['name'],
        'Symbol': crypto['symbol'],
        'Price (USD)': crypto['quote']['USD']['price'],
        'Market Cap (USD)': crypto['quote']['USD']['market_cap'],
        'Volume 24h (USD)': crypto['quote']['USD']['volume_24h'],
        'Percent Change 1h (%)': crypto['quote']['USD']['percent_change_1h'],
        'Percent Change 24h (%)': crypto['quote']['USD']['percent_change_24h'],
        'Percent Change 7d (%)': crypto['quote']['USD']['percent_change_7d'],
        'Circulating Supply': crypto['circulating_supply'],
        'Total Supply': crypto['total_supply'],
        'Max Supply': crypto.get('max_supply', None),  # Puede no estar presente
        'Last Updated': crypto['last_updated']
    })

# Crear el DataFrame
df = pd.DataFrame(cryptos_data)

# Mostrar las primeras filas del DataFrame
print(df.head())

# Para ver todas las variables del dataframe
print(df.columns)

          Name Symbol   Price (USD)  Market Cap (USD)  Volume 24h (USD)  \
0      Bitcoin    BTC  97484.697310      1.930044e+12      9.722166e+10   
1     Ethereum    ETH   3417.930184      4.116992e+11      5.887919e+10   
2  Tether USDt   USDT      0.999318      1.405336e+11      2.362281e+11   
3          XRP    XRP      2.248882      1.287539e+11      2.302030e+10   
4          BNB    BNB    666.569357      9.599125e+10      2.806454e+09   

   Percent Change 1h (%)  Percent Change 24h (%)  Percent Change 7d (%)  \
0              -0.617574               -2.672486              -2.545365   
1              -0.918284               -5.571133             -11.961841   
2               0.021569               -0.035776              -0.076450   
3              -1.371359               -2.362790              -3.984588   
4              -1.273102               -3.061993              -5.564063   

   Circulating Supply         Total Supply    Max Supply  \
0        1.979843e+07             1979

### Tercera API: CryptoCompare

In [5]:
import requests

response = requests.get(
    "https://min-api.cryptocompare.com/data/v2/news/",
    params={"lang":"EN","api_key":"76e0850532f6a9e0faa1926f9e4af3ceb15224cfb75e8f8638ab876bfa7547ad"},
    headers={"Content-type":"application/json; charset=UTF-8"}
)

json_response = response.json()
print(json_response)

{'Type': 100, 'Message': 'News list successfully returned', 'Promoted': [], 'Data': [{'id': '37859396', 'guid': 'https://www.cryptointelligence.co.uk/?p=26784', 'published_on': 1734652620, 'imageurl': 'https://resources.cryptocompare.com/news/95/default.png', 'title': 'Musk Loves Bitcoin (MUSKBTC) Solana Memecoin to Skyrocket 13,000% Before Exchange Listing, While Shiba Inu, BONK and Dogecoin Underperform', 'url': 'https://www.cryptointelligence.co.uk/musk-loves-bitcoin-muskbtc-solana-memecoin-to-skyrocket-13000-before-exchange-listing-while-shiba-inu-bonk-and-dogecoin-underperform/', 'body': 'Musk Loves Bitcoin could turn early investors into multi-millionaires, like Shiba Inu (SHIB) and Dogecoin (DOGE) did. Musk Loves Bitcoin (MUSKBTC), a new Solana memecoin that was launched today, is set to explode over 13,000% in price in the coming days. This is because MUSKBTC is set to soon be listed on numerous crypto exchanges, according to reports. This will give the Solana memecoin exposure

In [6]:
import pandas as pd
# Convertir a DataFrame si hay datos
if "Data" in json_response:
    df_news = pd.DataFrame(json_response["Data"])

    # Seleccionar solo columnas importantes
    df_news = df_news[["title", "source", "published_on", "url", "body"]]
    print(df_news.head())
else:
    print("No hay datos para mostrar.")

                                               title              source  \
0  Musk Loves Bitcoin (MUSKBTC) Solana Memecoin t...  cryptointelligence   
1  Bitcoin Price Crash: Will BTC Sell Off Continu...            coingape   
2  How Crypto And Web3 Can Help Fix The Broken U....              forbes   
3  Worldcoin Appeals Bavarian GDPR Ruling Amid Re...            coinotag   
4  Everything You Need to Know About the ‘Tomarke...             decrypt   

   published_on                                                url  \
0    1734652620  https://www.cryptointelligence.co.uk/musk-love...   
1    1734652459  https://coingape.com/bitcoin-price-crash-will-...   
2    1734652352  https://www.forbes.com/sites/chrissamcfarlane/...   
3    1734651933  https://en.coinotag.com/worldcoin-appeals-bava...   
4    1734651362  https://decrypt.co/289372/tomarket-telegram-ga...   

                                                body  
0  Musk Loves Bitcoin could turn early investors ...  
1  Bitcoin’s

## 3. Fusión Data frames (CoinGeko y Coinmarketcap)

### 3.1 Data frame de fusión de datos duplicados

Se fusionan (concatenan) ambos data frames, sin importar las monedas duplicadas.

In [14]:
import os
import pandas as pd

# Filtrar y renombrar columnas en CoinMarketCap
columnas_cmc = [
    'Name', 'Symbol', 'Price (USD)', 'Market Cap (USD)', 'Volume 24h (USD)',
    'Percent Change 24h (%)', 'Circulating Supply', 'Total Supply', 'Max Supply', 'Last Updated'
]
columnas_cmc_existentes = [col for col in columnas_cmc if col in df.columns]

df_filtered = df[columnas_cmc_existentes].copy()
df_filtered.rename(columns={
    'Last Updated': 'Last Update (DATE)',
    'Max Supply': 'Max Supply',
    'Total Supply': 'Total Supply',
}, inplace=True)
df_filtered['Source'] = 'CoinMarketCap'

# Filtrar y renombrar columnas en CoinGecko
columnas_cg = [
    'id', 'name', 'symbol', 'current_price', 'market_cap', 'total_volume',
    'price_change_percentage_24h', 'circulating_supply', 'ath', 'market_cap_rank',
    'max_supply', 'ath_date', 'total_supply', 'last_updated'
]
columnas_cg_existentes = [col for col in columnas_cg if col in df_monedas.columns]

df_monedas_filtered = df_monedas[columnas_cg_existentes].copy()
df_monedas_filtered.rename(columns={
    'id': 'ID',
    'name': 'Name',
    'symbol': 'Symbol',
    'current_price': 'Price (USD)',
    'market_cap': 'Market Cap (USD)',
    'total_volume': 'Volume 24h (USD)',
    'price_change_percentage_24h': 'Percent Change 24h (%)',
    'circulating_supply': 'Circulating Supply',
    'max_supply': 'Max Supply',
    'last_updated': 'Last Update (DATE)',
    'total_supply': 'Total Supply',
}, inplace=True)
df_monedas_filtered['Source'] = 'CoinGecko'

# Concatenar ambos DataFrames y eliminar duplicados basados en el símbolo
df_combined = pd.concat([df_monedas_filtered, df_filtered], ignore_index=True)

# Definir las columnas finales y validar su existencia en el DataFrame combinado
columnas_finales = [
    'Name', 'Symbol', 'Price (USD)', 'Market Cap (USD)', 'Volume 24h (USD)',
    'Percent Change 24h (%)', 'Circulating Supply', 'Total Supply', 'Max Supply',
    'Last Update (DATE)', 'Source'
]
columnas_finales_existentes = [col for col in columnas_finales if col in df_combined.columns]

# Reorganizar columnas finales
df_combined = df_combined[columnas_finales_existentes]

output_dir = "CSVs"
os.makedirs(output_dir, exist_ok=True)  # Crear el directorio si no existe

csv_filename = f"{output_dir}/crypto_data_19_12_2024_19_04pm.csv"
df_combined.to_csv(csv_filename, index=False)

print(f"Archivo CSV guardado en: {csv_filename}")


Archivo CSV guardado en: CSVs/crypto_data_19_12_2024_19_04pm.csv


### 3.2 Data frame de fusión de datos NO duplicados

In [15]:

# Imprimir columnas actuales en ambos DataFrames para ver qué columnas existen realmente
print("Columnas en df (CoinMarketCap):", df.columns.tolist())
print("Columnas en df_monedas (CoinGecko):", df_monedas.columns.tolist())

# Definir las columnas relevantes para CoinMarketCap
columnas_cmc = [
    'Name', 'Symbol', 'Price (USD)', 'Market Cap (USD)', 'Volume 24h (USD)',
    'Percent Change 24h (%)', 'Circulating Supply', 'Total Supply', 'Max Supply', 'Last Updated'
]

# Validar y seleccionar solo columnas existentes en df
columnas_cmc_existentes = [col for col in columnas_cmc if col in df.columns]
print("Columnas seleccionadas en df (CoinMarketCap):", columnas_cmc_existentes)

# Filtrar y renombrar columnas en CoinMarketCap
df_filtered = df[columnas_cmc_existentes].copy()
df_filtered.rename(columns={
    'Last Updated': 'Last Update (DATE)',  # Cambiar a "Last Update (DATE)"
    'Max Supply': 'Max Supply',
    'Total Supply': 'Total Supply',  # Agregar la columna Total Supply
}, inplace=True)
df_filtered['Source'] = 'CoinMarketCap'

# Definir las columnas relevantes para CoinGecko
columnas_cg = [
    'id', 'name', 'symbol', 'current_price', 'market_cap', 'total_volume',
    'price_change_percentage_24h', 'circulating_supply', 'max_supply', 'ath', 'market_cap_rank',
    'ath_date', 'total_supply', 'last_updated'
]

# Validar y seleccionar solo columnas existentes en df_monedas
columnas_cg_existentes = [col for col in columnas_cg if col in df_monedas.columns]
print("Columnas seleccionadas en df_monedas (CoinGecko):", columnas_cg_existentes)

# Filtrar y renombrar columnas en CoinGecko
df_monedas_filtered = df_monedas[columnas_cg_existentes].copy()
df_monedas_filtered.rename(columns={
    'id': 'ID',
    'name': 'Name',
    'symbol': 'Symbol',
    'current_price': 'Price (USD)',
    'market_cap': 'Market Cap (USD)',
    'total_volume': 'Volume 24h (USD)',
    'price_change_percentage_24h': 'Percent Change 24h (%)',
    'circulating_supply': 'Circulating Supply',
    'max_supply': 'Max Supply',
    'last_updated': 'Last Update (DATE)',
    'total_supply': 'Total Supply',  # Agregar la columna Total Supply
}, inplace=True)
df_monedas_filtered['Source'] = 'CoinGecko'

# Concatenar ambos DataFrames y eliminar duplicados basados en el símbolo
df_combined2 = pd.concat([df_monedas_filtered, df_filtered], ignore_index=True)

# Eliminar duplicados basados en el símbolo
df_combined2 = df_combined2.drop_duplicates(subset=['Symbol'])

# Definir las columnas finales y validar su existencia en el DataFrame combinado
columnas_finales = [
    'Name', 'Symbol', 'Price (USD)', 'Market Cap (USD)', 'Volume 24h (USD)',
    'Percent Change 24h (%)', 'Circulating Supply', 'Total Supply', 'Max Supply',
    'Last Update (DATE)', 'Source'
]
columnas_finales_existentes = [col for col in columnas_finales if col in df_combined2.columns]

# Reorganizar columnas finales
df_combined2 = df_combined2[columnas_finales_existentes]



output_dir = "CSVs"
os.makedirs(output_dir, exist_ok=True)  # Crear el directorio si no existe

csv_filename = f"{output_dir}/crypto_data_no_duplicada_19_12_2024_19_07pm.csv"
df_combined.to_csv(csv_filename, index=False)

print(f"Archivo CSV guardado en: {csv_filename}")


# Mostrar el resultado
print(df_combined2)

Columnas en df (CoinMarketCap): ['Name', 'Symbol', 'Price (USD)', 'Market Cap (USD)', 'Volume 24h (USD)', 'Percent Change 1h (%)', 'Percent Change 24h (%)', 'Percent Change 7d (%)', 'Circulating Supply', 'Total Supply', 'Max Supply', 'Last Updated']
Columnas en df_monedas (CoinGecko): ['id', 'symbol', 'name', 'image', 'current_price', 'market_cap', 'market_cap_rank', 'fully_diluted_valuation', 'total_volume', 'high_24h', 'low_24h', 'price_change_24h', 'price_change_percentage_24h', 'market_cap_change_24h', 'market_cap_change_percentage_24h', 'circulating_supply', 'total_supply', 'max_supply', 'ath', 'ath_change_percentage', 'ath_date', 'atl', 'atl_change_percentage', 'atl_date', 'roi', 'last_updated']
Columnas seleccionadas en df (CoinMarketCap): ['Name', 'Symbol', 'Price (USD)', 'Market Cap (USD)', 'Volume 24h (USD)', 'Percent Change 24h (%)', 'Circulating Supply', 'Total Supply', 'Max Supply', 'Last Updated']
Columnas seleccionadas en df_monedas (CoinGecko): ['id', 'name', 'symbol', 

## 4. Análisis de datos (CoinGeko y Coinmarketcap)

### 4.1 Medidas de Tendencia Central

#### 4.1.1 MEDIDAS DE TENDENCIA CENTRAL PARA DATA FRAME con datos duplicados

In [9]:
print("Media del precio (USD):", df_combined['Price (USD)'].mean()) # se obtiene la media
print("Mediana del precio (USD):", df_combined['Price (USD)'].median()) # se obtiene la mediana
print("Moda del precio (USD):", df_combined['Price (USD)'].mode().iloc[0]) # se obtiene la moda

Media del precio (USD): 192.98046108519605
Mediana del precio (USD): 0.017237728719291176
Moda del precio (USD): 0.0007125552791815131


#### 4.1.2 MEDIDAS DE TENDENCIA CENTRAL PARA DATA FRAME con datos NO duplicados

In [10]:
print("Media del precio (USD):", df_combined2['Price (USD)'].mean()) # se obtiene la media
print("Mediana del precio (USD):", df_combined2['Price (USD)'].median()) # se obtiene la mediana
print("Moda del precio (USD):", df_combined2['Price (USD)'].mode().iloc[0]) # se obtiene la moda

Media del precio (USD): 207.58080083578332
Mediana del precio (USD): 0.019382515711704774
Moda del precio (USD): 0.0007125552791815131


### 4.2  Análisis y comparaciones

In [11]:
import pandas as pd

# Definición de la función `custom_stats` para calcular estadísticas personalizadas en grupos.
def custom_stats(group):
    """
    Calcula estadísticas personalizadas para un grupo de datos.

    Parámetros:
    - group: pd.Series, una serie que contiene los datos de un grupo específico.

    Retorna:
    - pd.Series: Una serie que contiene las estadísticas calculadas:
        - 'mean': La media de los valores del grupo.
        - 'median': La mediana de los valores del grupo.
        - 'mode': La moda de los valores del grupo. Si no hay moda, devuelve None.
    """
    return pd.Series({
        'mean': group.mean(),  # Calcula la media del grupo.
        'median': group.median(),  # Calcula la mediana del grupo.
        'mode': group.mode().iloc[0] if not group.mode().empty else None  # Calcula la moda, o None si no hay moda.
    })

# Agrupa el DataFrame `df_combined` por la columna 'Source' y aplica la función `custom_stats` a la columna 'Price (USD)'.
# Esto genera estadísticas personalizadas para cada grupo definido por 'Source'.
grouped = df_combined.groupby('Source')['Price (USD)'].apply(custom_stats)

# Imprime el resultado agrupado con las estadísticas calculadas.
print(grouped)

Source               
CoinGecko      mean      1319.503112
               median       0.507843
               mode         1.510000
CoinMarketCap  mean       114.374214
               median       0.012866
               mode         0.000713
Name: Price (USD), dtype: float64


## 5. VISUALIZACIÓN

### 5.1  Top 10 de criptomonedas con más valor

In [16]:
import plotly.express as px

# Asegurarnos de que 'Market Cap (USD)' esté en formato numérico
df_combined2['Market Cap (USD)'] = pd.to_numeric(df_combined2['Market Cap (USD)'], errors='coerce')

# Convertir 'Market Cap (USD)' a millones
df_combined2['Market Cap (MM USD)'] = df_combined2['Market Cap (USD)'] / 1_000_000_000

# Ordenar el DataFrame por 'Market Cap (USD)' en millones de mayor a menor y seleccionar las top 20
top_10_cryptos = df_combined2.sort_values(by='Market Cap (MM USD)', ascending=False ).head(10)

# Crear gráfico de barras horizontales usando Plotly
fig = px.bar(
    top_10_cryptos,
    y='Name',  # Nombre de la criptomoneda en el eje Y
    x='Market Cap (MM USD)',  # Valor de Market Cap en millones en el eje X
    orientation='h',  # Barras horizontales
    title='Top 10 Cryptocurrencies by Market Cap (in billions)',
    labels={'Name': 'Cryptocurrency', 'Market Cap (MM USD)': 'Market Cap (MM USD)'},
    hover_data={'Market Cap (MM USD)': ':,.1f'}  # Formato del tooltip con un decimal
)

# Actualizar el eje X para mostrar los valores en millones
fig.update_layout(
    xaxis_tickprefix="$",  # Prefijo de moneda
    xaxis_tickformat=".1f",  # Mostrar con un decimal
    yaxis_categoryorder='total ascending'  # Ordenar las barras de mayor a menor
)



# Guardar gráfico en una carpeta "graficos"
output_dir = "graficos"
os.makedirs(output_dir, exist_ok=True)  # Crear el directorio si no existe
fig.write_html(f"{output_dir}/top_10_cryptos_19_12_2024_19_09pm.html")

# Mostrar el gráfico
fig.show()

### 5.2  Personalización de data frame de CryptoCompare

In [13]:
from IPython.display import HTML

# Personalización de la salida de data frame para mayor legibilidad

# Verifica si la clave "Data" existe en el diccionario json_response. Esta clave contiene noticias devueltas por la API.
if "Data" in json_response: 
    
    #Se crea un dataframe con la lista de noticias que estan en el diccionario de Data
    df_news = pd.DataFrame(json_response["Data"]) 
    
    # Seleccionar solo columnas importantes
    df_news = df_news[["title", "source", "published_on", "url", "body"]]

    # Convierte la columna published_on (que está en formato timestamp UNIX, es decir, segundos desde 1970-01-01) a una fecha legible en pandas 
    df_news["published_on"] = pd.to_datetime(df_news["published_on"], unit="s")

    # Guardar la columna 'url' original para usarla en los enlaces de la columna 'body'
    url_column = df_news["url"].copy()

    # Usa una función lambda para transformar las URLs originales en enlaces HTML clicables:
    df_news["url"] = url_column.apply(
        lambda x: # La función lambda se aplica para cada elemento de url_column
        f'<a href="{x}" target="_blank">Abrir enlace</a>' 
        # El valor {x} será reemplazado por la URL actual.
        # target Indica que el enlace debe abrirse en una nueva pestaña o ventana del navegador.
    ) 
    
    # Mejorar la columna 'body': truncar texto y agregar un enlace "Leer más"
    def format_body(body, url):
        truncated_body = body[:100] + "..." if len(body) > 100 else body # Se trunca el contenido si es que hay más de 100 caracteres
        return f'{truncated_body} <a href="{url}" target="_blank">Leer más</a>' # Se añade un enlace HTML usando la URL

    # Aplicar el formato personalizado a la columna 'body'
    df_news["body"] = [format_body(body, url) for body, url in zip(df_news["body"], url_column)]

    # Ajustar opciones de pandas para mejor visualización
    pd.set_option("display.max_colwidth", None)  # Mostrar contenido completo en las columnas
    pd.set_option("display.width", 1000) # Ajustar el ancho de la tabla para evitar cortes de texto

    # Renderizar el DataFrame como HTML
    display(HTML(df_news.to_html(escape=False, index=False)))  # escape=False permite interpretar HTML
else:
    print("No hay datos para mostrar.")

Esto es un análisis inicial básico de todo lo que se puede con esta API. El API de Crytocompare puede usarse para leer las noticias en voz alta con 'pyttsx3' que es una API de texto de voz.
Generar graficos de popularidad de noticias según la fuente
Usa bibliotecas como tkinter o PySimpleGUI para crear una GUI donde el usuario pueda interactuar con las noticias.